In [1]:
import pandas as pd
import csv
from omegaconf import OmegaConf
import os
import sys
import monai.transforms as transforms
from monai.transforms import (
Orientationd, EnsureChannelFirst, Compose, ToTensord, Spacingd,Resized,ScaleIntensityD,ResizeWithPadOrCropd
# ScaleIntensityD, ScaleIntensityRangeD, AdjustContrastD, RandAffined, ToNumpyd,RepeatChannelD
)
import pandas as pd
from omegaconf import OmegaConf
import numpy as np
import os
# sys.path.insert(0,'/storage/Ayantika/Diffusion_AE_medical/')
# import dataset.slice_data_h5_ADNI_with_baseline as sdl
import sys
sys.path.insert(0,'/home/projects/medimg/ayantika/Ayantika/Diff_AE_xstart_w_xbsln_disentangle_unsup/dataset/')
import slice_data_h5_ADNI_ventricle_mask as sdl


# Custom MapTransform to work on dictionaries
class CustomEnsureChannelFirst(transforms.MapTransform):
    def __init__(self, keys):
        super().__init__(keys)
        self.ensure_channel_first = EnsureChannelFirst()

    def __call__(self, data):
        for key in self.keys:
            print(key)
            data[key] = self.ensure_channel_first(data[key])
        return data

class NormalizeIntensityByClippingD(transforms.MapTransform):
    def __init__(self, keys, percentile=99.5):
        super().__init__(keys)
        self.percentile = percentile

    def __call__(self, data):
        for key in self.keys:
            image = data[key]
            v_99_5 = np.percentile(image, self.percentile)
            image = np.clip(image, 0, v_99_5)
            data[key] = image
        return data

class ADNI_dataloader():
    def __init__(self,csv_path,path,h5_save_path):
        self.csv_path = csv_path
        self.path = path
        self.h5_save_path = h5_save_path

    # Define the custom transform

    def get_transform_nii_vols(self,key_list_image,key_list_label):
        print("in fuction",key_list_image+key_list_label)
#         tuple(key_list_image+key_list_label)
        transforms_ = Compose(
            [
             CustomEnsureChannelFirst(tuple(key_list_image+key_list_label)),
             Orientationd(tuple(key_list_image+key_list_label),'RAS'),
        #      Spacingd(('image','label'),(1,1,1)),        
             Resized(keys = (tuple(key_list_image)),spatial_size = (self.config.dataloader.img_height, self.config.dataloader.img_width,-1),\
                     mode = 'trilinear' ,align_corners = True),
             Resized(keys = (tuple(key_list_label)),spatial_size = (self.config.dataloader.img_height, self.config.dataloader.img_width,-1),\
                     mode = 'nearest' ),
             NormalizeIntensityByClippingD(tuple(key_list_image)),
             ScaleIntensityD(tuple(key_list_image), minv=-1, maxv=1),
             ToTensord(tuple(key_list_image+key_list_label)),
            ]
        )

        return transforms_
    
    
    def get_list_for_dataloader(self,tuple_,MCI_M_dict,key_='image'):
        datalist = {}
        list_for_dict = []
        for i,key in enumerate(tuple_):
        #     list_image_paths = glob.glob(conf.config.dataloader.training_path[i])
        #     list_image_paths.sort()
            for indx in range(0,len(MCI_M_dict['Subject'])):

                sub_indx_list = []
                for sub_indx in range(0,len(MCI_M_dict['Subject'])):
                    if (MCI_M_dict['Subject'][sub_indx] == MCI_M_dict['Subject'][indx]) and (MCI_M_dict['Age'][sub_indx] > MCI_M_dict['Age'][indx]):

                        sub_indx_list.append(sub_indx)

                if len(sub_indx_list)!=0:
                    indx_final = np.random.randint(0,len(sub_indx_list),1)[0]
                    indx_next_ = sub_indx_list[indx_final]
    #                 print(MCI_M_dict['Subject'][indx_next_] , MCI_M_dict['Subject'][indx])
    #                 print(MCI_M_dict['Age'][indx_next_] , MCI_M_dict['Age'][indx])

                else:
                    indx_next_ = indx

                key_final ='baseline_' + key_
                
                list_for_dict.append( \
                                     {key_final :MCI_M_dict['nii path'][indx],\
                                        key_:MCI_M_dict['nii path'][indx_next_],\
                                        'Subject': MCI_M_dict['Subject'][indx],\
                                        'baseline_Aquisition Date':MCI_M_dict['Aquisition Date'][indx],\
                                        'Aquisition Date':MCI_M_dict['Aquisition Date'][indx_next_],\
                                        'baseline_Age':MCI_M_dict['Age'][indx],\
                                        'Age':MCI_M_dict['Age'][indx_next_],\
                                        'Health status':MCI_M_dict['Health status'][indx],\
                                        'Description':MCI_M_dict['Description'][indx],\
                                        'Sex':MCI_M_dict['Sex'][indx],\
                                        'baseline nii path':MCI_M_dict['nii path'][indx],\
                                        'nii path':MCI_M_dict['nii path'][indx_next_],\
                                     })

            datalist.update({key:list_for_dict})
            return datalist
        
    def dict_list_csv(self,datalist,csv_file_name):    
        field_names = datalist['_train'][0].keys()

        with open(csv_file_name, mode='w',newline='') as csv_file:
            writer = csv.DictWriter(csv_file, fieldnames=field_names)

            # Write the header
            writer.writeheader()

            # Write the data rows
            for row in datalist['_train']:
                writer.writerow(row)
        
    def create_pair_info_csv(self, csv_file_name, csv_mask_name):
    
    
        MCI_M_csv = pd.read_csv( self.csv_path)
        MCI_M_dict = MCI_M_csv.to_dict()
        self.config_path = self.path
        self.config = OmegaConf.load(self.config_path)
#         self.config.dataloader.h5cachedir_ = '/storage/Ayantika/h5data_store_with_DiffAE_output'
            
        datalist = self.get_list_for_dataloader(self.config.dataloader.key_tuple_image,MCI_M_dict,key_='image')
        masklist = self.get_list_for_dataloader(self.config.dataloader.key_tuple_mask,MCI_M_dict,key_='label')
        
        self.dict_list_csv(datalist,csv_file_name)
        self.dict_list_csv(masklist,csv_mask_name)
        
    def make_dict_list_from_csv(self, csv_file_name,mode='train'):
        csv_file = pd.read_csv(csv_file_name)
        data_list = []

        # Open the CSV file for reading
        with open(csv_file_name, mode='r', newline='') as csv_file:
            reader = csv.DictReader(csv_file)

            # Iterate through the rows and append each row dictionary to the list
            for row in reader:
                data_list.append(row)



        return {'_'+mode:data_list}
        
    def main_call(self,csv_file_name,csv_mask_name,mode='train'):
        
        MCI_M_csv = pd.read_csv( self.csv_path)
        MCI_M_dict = MCI_M_csv.to_dict()
        self.config_path = self.path
        self.config = OmegaConf.load(self.config_path)
#         self.config.dataloader.h5cachedir_ = '/storage/Ayantika/h5data_store_with_DiffAE_output'
            
        datalist = self.make_dict_list_from_csv(csv_file_name,mode)
        masklist = self.make_dict_list_from_csv(csv_mask_name,mode)
        key_list_image = []
        key_list_label = []
        for keys_ in datalist.keys():
            key_list_image.append(str(keys_)+'_image')
            key_list_image.append(str(keys_)+'_baseline_image')
        for keys_ in masklist.keys():
            key_list_label.append(str(keys_)+'_label')
            key_list_label.append(str(keys_)+'_baseline_label')
        print(key_list_image,key_list_label)

        transforms_ = self.get_transform_nii_vols(key_list_image,key_list_label)
        self.config.dataloader.h5cachedir_ = self.h5_save_path
        ## The loader is such that it would create h5 files if they are not created when the loader is called and executed
        if not os.path.exists(self.config.dataloader.h5cachedir_):
            os.mkdir(self.config.dataloader.h5cachedir_)
        h5cacheds = sdl.H5CachedDataset(datalist,masklist,transforms_,h5cachedir= self.config.dataloader.h5cachedir_,\
                                           nslices_per_image=self.config.dataloader.total_slices_per_vol,\
                                           start_slice = self.config.dataloader.start_slice_per_vol,\
                                        end_slice = self.config.dataloader.end_slice_per_vol)
        return h5cacheds
        
        

ModuleNotFoundError: No module named 'omegaconf'

In [2]:

csv_train_loader = '/storage/ayantika/Ayantika/Data_final/ADNI_Data_loader_csv/ADNI_info_train_final_subset.csv'
csv_test_loader = '/storage/ayantika/Ayantika/Data_final/ADNI_Data_loader_csv/ADNI_info_test_final.csv'
config_path = '/storage/ayantika/Ayantika/Diffusion_AE_medical_cond/config_file_ADNI.yaml'
h5_save_path_train = '/storage/ayantika/Ayantika/h5data_store/ADNI_cond_train_ventricle_mask'
h5_save_path_test = '/storage/ayantika/Ayantika/h5data_store/ADNI_cond_test_ventricle_mask'

csv_file_name_train = '/storage/ayantika/Ayantika/Data_final/ADNI_Data_loader_csv/ADNI_train_pair_data_info.csv'
csv_mask_name_train = '/storage/ayantika/Ayantika/Data_final/ADNI_Data_loader_csv/ADNI_train_pair_mask_info.csv'

csv_file_name_test = '/storage/ayantika/Ayantika/Data_final/ADNI_Data_loader_csv/ADNI_test_pair_data_info.csv'
csv_mask_name_test = '/storage/ayantika/Ayantika/Data_final/ADNI_Data_loader_csv/ADNI_test_pair_mask_info.csv'

loader_cls = ADNI_dataloader(csv_train_loader,config_path,h5_save_path_train)

# loader_cls.create_pair_info_csv(csv_file_name ='/storage/ayantika/Ayantika/Data_final/ADNI_Data_loader_csv/ADNI_train_pair_data_info.csv',\
#                                 csv_mask_name = '/storage/ayantika/Ayantika/Data_final/ADNI_Data_loader_csv/ADNI_train_pair_mask_info.csv')



# loader_cls.create_pair_info_csv(csv_file_name ='/storage/ayantika/Ayantika/Data_final/ADNI_Data_loader_csv/ADNI_test_pair_data_info.csv',\
#                                 csv_mask_name = '/storage/ayantika/Ayantika/Data_final/ADNI_Data_loader_csv/ADNI_test_pair_mask_info.csv')
train_dataset = loader_cls.main_call(csv_file_name=csv_file_name_train,\
                     csv_mask_name=csv_mask_name_train,\
                     mode='train')


loader_cls = ADNI_dataloader(csv_test_loader,config_path,h5_save_path_test)
test_dataset = loader_cls.main_call(csv_file_name=csv_file_name_test,\
                     csv_mask_name=csv_mask_name_test,\
                     mode='test')


['_train_image', '_train_baseline_image'] ['_train_label', '_train_baseline_label']
in fuction ['_train_image', '_train_baseline_image', '_train_label', '_train_baseline_label']
['_test_image', '_test_baseline_image'] ['_test_label', '_test_baseline_label']
in fuction ['_test_image', '_test_baseline_image', '_test_label', '_test_baseline_label']


In [3]:
# !rm -r '/storage/ayantika/Ayantika/h5data_store/ADNI_cond_train_ventricle_mask'
# !rm -r '/storage/ayantika/Ayantika/h5data_store/ADNI_cond_test_ventricle_mask'

In [4]:




from torch.utils.data import DataLoader
train_loader = DataLoader(
                train_dataset,
                batch_size = 10,
                shuffle=True)


test_loader = DataLoader(
                test_dataset,
                batch_size = 10,
                shuffle=True)


In [53]:
from tqdm import tqdm
# iter_ = 
for i,batch in tqdm((enumerate(test_loader)),total=len(test_loader)):
    print(batch.keys())

  0%|                                                                                                                | 0/3110 [00:00<?, ?it/s]

/storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/131_S_0384_84.1_84.1_75.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/131_S_0384_84.1_84.1_75.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/114_S_0458_83.6_83.0_101.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/027_S_1385_71.6_70.2_61.pt
/storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/027_S_0835_75.9_73.4_107.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/027_S_0835_75.9_73.4_107.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/023_S_0376_71.1_70.7_109.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/033_S_0889_74.7_73.6_95.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/036_S_0576_78.1_77.6_87.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/062_S_1099_79

  0%|                                                                                                      | 1/3110 [00:02<2:01:03,  2.34s/it]

ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/023_S_1262_73.9_73.4_79.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/023_S_0376_74.7_73.7_81.pt
dict_keys(['_test_baseline_image', '_test_baseline_label', '_test_image', '_test_label', 'image_meta_dict', 'ventricle_mask', 'slicenum', 'idx', 'Subject', 'Aquisition Date', 'baseline Aquisition Date', 'Age', 'baseline Age', 'Description', 'nii path', 'baseline nii path', 'Sex', 'Health status'])
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/027_S_0835_74.9_73.9_82.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/023_S_0926_74.3_72.3_103.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/023_S_0926_73.3_71.2_68.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/005_S_0324_78.6_76.0_107.pt
/storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/114_S_0416_

  0%|                                                                                                      | 2/3110 [00:04<1:48:29,  2.09s/it]

...

 78%|█████████████████████████████████████████████████████████████████████████████▏                     | 2424/3110 [1:12:10<26:06,  2.28s/it]

ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/041_S_0314_74.3_72.2_97.pt
dict_keys(['_test_baseline_image', '_test_baseline_label', '_test_image', '_test_label', 'image_meta_dict', 'ventricle_mask', 'slicenum', 'idx', 'Subject', 'Aquisition Date', 'baseline Aquisition Date', 'Age', 'baseline Age', 'Description', 'nii path', 'baseline nii path', 'Sex', 'Health status'])
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/011_S_0362_74.7_72.1_83.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/057_S_0818_75.1_74.1_64.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/941_S_1202_79.6_78.2_72.pt
/storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/062_S_0793_71.3_71.3_60.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/062_S_0793_71.3_71.3_60.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/024_S_1307_77

 78%|█████████████████████████████████████████████████████████████████████████████▏                     | 2425/3110 [1:12:11<23:05,  2.02s/it]

ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/051_S_1331_78.0_77.9_87.pt
ventricle_mask_path /storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/136_S_0186_84.8_84.8_99.pt
dict_keys(['_test_baseline_image', '_test_baseline_label', '_test_image', '_test_label', 'image_meta_dict', 'ventricle_mask', 'slicenum', 'idx', 'Subject', 'Aquisition Date', 'baseline Aquisition Date', 'Age', 'baseline Age', 'Description', 'nii path', 'baseline nii path', 'Sex', 'Health status'])


IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [7]:
os.path.exists('/storage/ayantika/Ayantika/Data_final/MCI_data/MCI_Regis/036_S_0869/MPR__GradWarp__B1_Correction__N3__Scaled/2010-11-11_12_45_45.0/I219067/ADNI_036_S_0869_MR_MPR__GradWarp__B1_Correction__N3__Scaled_Br_20110222141716719_S94833_I219067.nii')

False

In [25]:
# torch.load('/storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/027_S_0461_81.9_81.5_69.pt')
csv_ff = pd.read_csv('/storage/ayantika/Ayantika/Data_final/ADNI_Data_loader_csv/ADNI_test_pair_data_info.csv')
csv_ff['Age'][np.where(np.array(list(csv_ff['Subject']))== '027_S_0461')[0][0::]]

427    81.9
428    81.9
429    81.5
430    81.5
Name: Age, dtype: float64

In [52]:
# problematic_files

In [51]:
# !rm -r '/storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/023_S_1262_74.9_73.9_72.pt'

In [47]:
import glob
glob_list = glob.glob('/storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/**')
problematic_files = []
for iii in tqdm(glob_list):
    if os.path.exists(iii):
        try:
            torch.load(iii)
        except EOFError:
            print(iii)
            problematic_files.append(iii)
#         torch.load(iii)

 57%|████████████████████████████████████████████████████████▏                                          | 20813/36671 [04:18<03:11, 82.80it/s]

/storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/082_S_0469_78.7_78.6_94.pt


 99%|█████████████████████████████████████████████████████████████████████████████████████████████████▌ | 36159/36671 [07:58<00:06, 83.30it/s]

/storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/023_S_1262_74.9_73.9_72.pt


100%|███████████████████████████████████████████████████████████████████████████████████████████████████| 36671/36671 [08:05<00:00, 75.47it/s]


In [44]:
file_path = '/storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/082_S_0469_78.7_78.6_94.pt'



In [45]:
problematic_files

['/storage/ayantika/Ayantika/Data_final/ADNI_ventricle_mask/082_S_0469_78.7_78.6_94.pt']

In [34]:
from monai.transforms import Compose, LoadImageD, EnsureChannelFirstd, LoadImaged, MapTransform

In [20]:
img,meta_data = load_image('/storage/ayantika/Ayantika/Data_final/MCI_data/MCI_Regis/002_S_0729/MPR-R__GradWarp__B1_Correction__N3__Scaled/2008-04-03_14_09_47.0/I121067/ADNI_002_S_0729_MR_MPR-R__GradWarp__B1_Correction__N3__Scaled_Br_20081015150059952_S48530_I121067.nii')

In [32]:
# tt=EnsureChannelFirstd(('img','meta_dict'))
# tt({'img':img,'meta_dict':meta_data})


In [47]:
# Custom MapTransform to work on dictionaries
class CustomEnsureChannelFirst(MapTransform):
    def __init__(self, keys):
        super().__init__(keys)
        self.ensure_channel_first = EnsureChannelFirst()

    def __call__(self, data):
        for key in self.keys:
            print(key)
            data[key] = self.ensure_channel_first(data[key])
        return data

# Define the transforms
transforms = Compose([
#     LoadImage(image_only=False),  # Load image with metadata
    CustomEnsureChannelFirst(keys=['image'])  # Ensure channel first dimension
])

# # Simulate data loading
# data = {'img_path': img_path}
# image, meta = simulate_load_image(data['img_path'])
data_dict = {'image': img, 'image_meta_dict': meta_data}

# Apply transforms
transformed_data = transforms(data_dict)


image


In [48]:
transformed_data

{'image': metatensor([[[0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          ...,
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.]],
 
         [[0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          ...,
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.]],
 
         [[0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          ...,
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.]],
 
         ...,
 
         [[0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          [0., 0., 0.,  ..., 0., 0., 0.],
          ...,
          [0., 0., 0